In [263]:
import pandas as pd
from scipy.stats import norm
import numpy as np
import plotly.graph_objs as go
import plotly.express as px
import pystable

# Get Data

Coinbase data (treated)

In [208]:
coin_df = pd.read_csv('risk_pipeline/outputs/data/ETH-BTC_2022-06-01-00-00_2022-10-31-00-00_600secs_treated.csv', index_col=0)

In [209]:
coin_df.head()

time     close
0  2022-06-01 00:00:00  0.061110
1  2022-06-01 00:10:00  0.061075
2  2022-06-01 00:20:00  0.060915
3  2022-06-01 00:30:00  0.060985
4  2022-06-01 00:40:00  0.061020

In [210]:
# invert close to match uni v3
coin_df.close = 1/coin_df.close

Uniswap data

In [211]:
uni_df = pd.read_csv('../csv/WBTC-WETH-10.0mTWAP-14881677-to-15864319.csv', index_col=0)

In [212]:
uni_df.head()

timestamp       twap
0   2022-06-01 00:01:54  16.335589
2   2022-06-01 00:11:54  16.345683
4   2022-06-01 00:21:54  16.351692
10  2022-06-01 00:31:54  16.361773
11  2022-06-01 00:41:54  16.366600

In [213]:
uni_df.reset_index(inplace=True)

# Sanity checks

In [214]:
uni_df[uni_df.twap.isna()]

Empty DataFrame
Columns: [index, timestamp, twap]
Index: []

In [215]:
coin_df[coin_df.close.isna()]

Empty DataFrame
Columns: [time, close]
Index: []

In [216]:
print('shape:', uni_df.shape)
print('first timestamp:', uni_df.timestamp.min())
print('last timestamp:', uni_df.timestamp.max())

shape: (21883, 3)
first timestamp: 2022-06-01 00:01:54
last timestamp: 2022-10-30 23:01:54


In [217]:
print('shape:', coin_df.shape)
print('first timestamp:', coin_df.time.min())
print('last timestamp:', coin_df.time.max())

shape: (21889, 2)
first timestamp: 2022-06-01 00:00:00
last timestamp: 2022-10-31 00:00:00


# Combine data

In [218]:
df = pd.concat([coin_df.time, coin_df.close, uni_df.twap], axis=1)

In [219]:
df

time      close       twap
0      2022-06-01 00:00:00  16.363934  16.335589
1      2022-06-01 00:10:00  16.373312  16.345683
2      2022-06-01 00:20:00  16.416318  16.351692
3      2022-06-01 00:30:00  16.397475  16.361773
4      2022-06-01 00:40:00  16.388069  16.366600
...                    ...        ...        ...
21884  2022-10-30 23:20:00  12.971010        NaN
21885  2022-10-30 23:30:00  12.965124        NaN
21886  2022-10-30 23:40:00  12.977743        NaN
21887  2022-10-30 23:50:00  12.965964        NaN
21888  2022-10-31 00:00:00  12.969328        NaN

[21889 rows x 3 columns]

In [220]:
# Change column names
df.columns = ['time', 'coin', 'uni']

In [221]:
print('NAs in coinbase column =', df[df.coin.isna()].count()[0])
print('NAs in uniswap column =', df[df.uni.isna()].count()[0])


NAs in coinbase column = 0
NAs in uniswap column = 6


In [222]:
df.dropna(inplace=True)

In [223]:
df

time       coin        uni
0      2022-06-01 00:00:00  16.363934  16.335589
1      2022-06-01 00:10:00  16.373312  16.345683
2      2022-06-01 00:20:00  16.416318  16.351692
3      2022-06-01 00:30:00  16.397475  16.361773
4      2022-06-01 00:40:00  16.388069  16.366600
...                    ...        ...        ...
21878  2022-10-30 22:20:00  13.005592  12.995307
21879  2022-10-30 22:30:00  12.997141  12.995306
21880  2022-10-30 22:40:00  12.990387  12.995304
21881  2022-10-30 22:50:00  12.971851  12.995304
21882  2022-10-30 23:00:00  12.983641  12.995304

[21883 rows x 3 columns]

# Analysis

In [224]:
def line_chart(df, title, xcol, ycol, x_title, y_title):
    fig = px.line(df, x=xcol, y=ycol)
    fig.update_layout(title=title)
    fig.update_layout(xaxis_title=x_title, yaxis_title=y_title)
    return fig

In [225]:
# Superimposed plot
plt = line_chart(df, 'Prices', 'time', ['coin', 'uni'], 'Time', 'Prices')
plt.show()

In [226]:
# Pystable funcs

def gaussian():
    return pystable.create(alpha=2.0, beta=0.0, mu=0.0,
                           sigma=1.0, parameterization=1)

def get_qs(dst):
    l = [i/100 for i in range(1, 100, 1)]
    return pystable.q(dst, l, len(l))

def pdf(dst, vals):
    return pystable.pdf(dst, vals, len(vals))

def log_returns(p):
    return [np.log(p[i]/p[i-1]) for i in range(1, len(p))]


In [227]:
# Data funcs
def get_qs_data(series):
    l = [i for i in range(1, 100, 1)]
    return [np.percentile(series, i) for i in l]

In [228]:
log_coin = log_returns(df['coin'])
log_uni = log_returns(df['uni'])

In [229]:
dst_coin = gaussian()
pystable.fit(dst_coin, log_coin, len(log_coin))

dst_uni = gaussian()
pystable.fit(dst_uni, log_uni, len(log_uni))

0

In [230]:
coin_q = get_qs(dst_coin)
uni_q = get_qs(dst_uni)

In [231]:
dist_df = pd.DataFrame(
    {'Percentage': [i/100 for i in range(1, 100, 1)],
     'coin': coin_q, 'uni': uni_q}
)

In [232]:
plt = line_chart(dist_df, 'CDFs', 'Percentage', ['coin', 'uni'], 'Percentage', 'Log returns')
plt.show()

In [233]:
df['uni_log_returns'] = [0] + log_uni
df['coin_log_returns'] = [0] + log_coin


In [234]:
fig = px.histogram(df, x=['uni_log_returns'])
fig.show()

In [235]:
fig = px.histogram(df, x=['coin_log_returns'])
fig.show()

Uni distribution has way too many zeros. Maybe pystable is not able to fit the distribution. Check qq plot

In [236]:
uni_q_data = get_qs_data(log_uni)
fig = line_chart(pd.DataFrame({'data': uni_q_data, 'dist': uni_q}), 'Uni QQ plot', 'dist', 'data', 'Dist', 'Data')
fig.show()

In [237]:
coin_q_data = get_qs_data(log_coin)
fig = line_chart(pd.DataFrame({'data': coin_q_data, 'dist': coin_q}), 'Coin QQ plot', 'dist', 'data', 'Dist', 'Data')
fig.show()

# Try adding noise

In [247]:
noise_df = df.copy(deep=True)
noise_df = noise_df.iloc[1:,:]  # Remove first row since log returns are NA

In [248]:
noise_df

time       coin        uni  uni_log_returns  \
1      2022-06-01 00:10:00  16.373312  16.345683     6.177501e-04   
2      2022-06-01 00:20:00  16.416318  16.351692     3.675261e-04   
3      2022-06-01 00:30:00  16.397475  16.361773     6.163437e-04   
4      2022-06-01 00:40:00  16.388069  16.366600     2.949345e-04   
5      2022-06-01 00:50:00  16.362595  16.366600     0.000000e+00   
...                    ...        ...        ...              ...   
21878  2022-10-30 22:20:00  13.005592  12.995307     0.000000e+00   
21879  2022-10-30 22:30:00  12.997141  12.995306    -1.136248e-07   
21880  2022-10-30 22:40:00  12.990387  12.995304    -1.136248e-07   
21881  2022-10-30 22:50:00  12.971851  12.995304     0.000000e+00   
21882  2022-10-30 23:00:00  12.983641  12.995304     0.000000e+00   

       coin_log_returns  
1              0.000573  
2              0.002623  
3             -0.001148  
4             -0.000574  
5             -0.001556  
...                 ...  
21878         -0.001692  
21879         -0.000650  
21880         -0.000520  
21881         -0.001428  
21882          0.000908  

[21882 rows x 5 columns]

In [258]:
# Found out the percentage difference between uniswap and coinbase prices
noise_df['uni_coin_diff'] = noise_df.uni/noise_df.coin - 1
noise_df

time       coin        uni  uni_log_returns  \
1      2022-06-01 00:10:00  16.373312  16.345683     6.177501e-04   
2      2022-06-01 00:20:00  16.416318  16.351692     3.675261e-04   
3      2022-06-01 00:30:00  16.397475  16.361773     6.163437e-04   
4      2022-06-01 00:40:00  16.388069  16.366600     2.949345e-04   
5      2022-06-01 00:50:00  16.362595  16.366600     0.000000e+00   
...                    ...        ...        ...              ...   
21878  2022-10-30 22:20:00  13.005592  12.995307     0.000000e+00   
21879  2022-10-30 22:30:00  12.997141  12.995306    -1.136248e-07   
21880  2022-10-30 22:40:00  12.990387  12.995304    -1.136248e-07   
21881  2022-10-30 22:50:00  12.971851  12.995304     0.000000e+00   
21882  2022-10-30 23:00:00  12.983641  12.995304     0.000000e+00   

       coin_log_returns  uni_coin_diff  
1              0.000573      -0.001687  
2              0.002623      -0.003937  
3             -0.001148      -0.002177  
4             -0.000574      -0.001310  
5             -0.001556       0.000245  
...                 ...            ...  
21878         -0.001692      -0.000791  
21879         -0.000650      -0.000141  
21880         -0.000520       0.000379  
21881         -0.001428       0.001808  
21882          0.000908       0.000898  

[21882 rows x 6 columns]

In [259]:
# Average percentage price difference is expected to be ~0 since basically the prices are very similar
noise_df.uni_coin_diff.mean()

1.8854669752077555e-05

In [260]:
# Plot distribution of price difference. Expected to be gaussian
px.histogram(noise_df, x='uni_coin_diff')

In [262]:
mean, std_dev = norm.fit(noise_df.uni_coin_diff)
print('Mean =', mean)
print('Std Dev =', std_dev)

Mean = 1.8854669752077555e-05
Std Dev = 0.0025371914816321155


In [265]:
# plot the histogram of the data
histogram = go.Histogram(x=noise_df.uni_coin_diff, nbinsx=500, histnorm='probability density', opacity=0.5)
x = np.linspace(noise_df.uni_coin_diff.min(), noise_df.uni_coin_diff.max(), 100)
pdf = norm.pdf(x, loc=mean, scale=std_dev)
line = go.Scatter(x=x, y=pdf, mode='lines')
fig = go.Figure(data=[histogram, line])

# update the layout
fig.update_layout(title='Histogram with PDF', xaxis_title='Value', yaxis_title='Probability density')

# show the plot
fig.show()


In [272]:
def gauss_data_point(mean, stddev, thresh):
    lower_bound = mean - 2*stddev
    upper_bound = mean + 2*stddev
    point = np.random.normal(loc=mean, scale=std_dev, size=1)
    while (point < lower_bound) | (point > upper_bound):
        point = np.random.normal(loc=mean, scale=std_dev, size=1)
    return point[0]

In [273]:
noise_df['uni_noisy'] = noise_df.uni.apply(
    lambda x: (gauss_data_point(mean, std_dev, 2) + 1) * x
)

In [274]:
gauss_data_point(mean, std_dev, 2)

-0.0012918226115495037

In [276]:
noise_df

time       coin        uni  uni_log_returns  \
1      2022-06-01 00:10:00  16.373312  16.345683     6.177501e-04   
2      2022-06-01 00:20:00  16.416318  16.351692     3.675261e-04   
3      2022-06-01 00:30:00  16.397475  16.361773     6.163437e-04   
4      2022-06-01 00:40:00  16.388069  16.366600     2.949345e-04   
5      2022-06-01 00:50:00  16.362595  16.366600     0.000000e+00   
...                    ...        ...        ...              ...   
21878  2022-10-30 22:20:00  13.005592  12.995307     0.000000e+00   
21879  2022-10-30 22:30:00  12.997141  12.995306    -1.136248e-07   
21880  2022-10-30 22:40:00  12.990387  12.995304    -1.136248e-07   
21881  2022-10-30 22:50:00  12.971851  12.995304     0.000000e+00   
21882  2022-10-30 23:00:00  12.983641  12.995304     0.000000e+00   

       coin_log_returns  uni_coin_diff  uni_noisy  
1              0.000573      -0.001687  16.363500  
2              0.002623      -0.003937  16.341475  
3             -0.001148      -0.002177  16.403184  
4             -0.000574      -0.001310  16.358264  
5             -0.001556       0.000245  16.422233  
...                 ...            ...        ...  
21878         -0.001692      -0.000791  13.014090  
21879         -0.000650      -0.000141  13.018972  
21880         -0.000520       0.000379  12.981344  
21881         -0.001428       0.001808  12.932610  
21882          0.000908       0.000898  13.005339  

[21882 rows x 7 columns]